# Instrumental Part tools

In [1]:
import sys
from math import *
import pandas as pd
import numpy as np
from numpy import fft
from scipy import signal
from scipy import *
import scipy

import LAPPTP_stream_lib
import matplotlib.pyplot as plt
#%matplotlib notebook
import GW_generator as GW

print('Importation done')

Importation done


## Calibration functions

In [4]:
# Linear function to calibrate the interferometer

def calib_inject(fsamp, u_min=0, u_max=5) :
    # Input: 
    #   fsamp : the sampling frequency (salar float)
    #   u_min and _max : the minimum and maximum voltagre given by the LabJack (scalar float)
    # return :
    #   voltage (as a list) : the voltage given by the labJack at each time step for a full second (list of float)
    
    voltage = np.linspace(u_min,u_max,fsamp)
    return voltage.tolist()

# Sine function to interpolate the calibration of the interferometer

def sinus_cal(x, A, omega, phase, B):
    # Input : 
    #   x : the input voltage of the labjack (scalar or list of float)
    #   A : the amplitude of the sine function (scalar float)
    #   omega : the sine frequency (scalar float)
    #   phase : the sine phase shift (scalar float)
    #   B : the voltage shift (scalar float)
    # return :
    #   y : the expected voltage in CCD ouput (scalar or list of float)
    
    y = A*np.sin(omega*x + phase) + B
    return y

# ArcSine function to "de-calibrate" the output signal and find the reconstructed signal

def arcsin_cal(y, A, omega, phase, B):
    # Input : 
    #   y : the output voltage of the CCD (scalar or list of float)
    #   A : the amplitude of the sine function (scalar float)
    #   omega : the sine frequency (scalar float)
    #   phase : the sine phase shift (scalar float)
    #   B : the voltage shift (scalar float)
    # return :
    #   x : the expected voltage in LabJack Input (scalar or list of float)
    
    x = (np.arcsin((y-B)/A)-phase)/omega
    return x

#  Make the signal saturate to avoid errors during the reconstruction of the signal

def saturation(data, min_val, max_val):
    # Input :
    #   data : the signal to saturate (list or np.array of float)
    #   min_val : minimum value allowed (scalar float)
    #   max_val : maximum value allowed (scalar float)
    
    amp_val = (max_val - min_val)/2.
    data_sat = np.zeros(len(data))
    for i in range(0,len(data)):
        if(data[i]>(max_val-2.e-15*amp_val)):
            data_sat[i] = max_val-2.e-15*amp_val
        elif(data[i]<(min_val+2.e-15*amp_val)) :
            data_sat[i] = min_val+2.e-15*amp_val
        else data_sat[i] = data[i]
    
    return data_sat.tolist()
    

## Read and write data in TXT

In [10]:
# Read the data from a text file

def Read_txt(name):
    # Input : 
    #   name : the name of the input file (string)
    # return :
    #   data : the list of the data in the txt file (list)
    
    with open(name, "r") as f :
        lines = f.readlines()
    
    data = [float(line) for line in lines]
    
    return data
    
# Write the data to a text file

def Write_txt(name, data):
    # Input :
    #   name : the name of the txt file in ouput (string)
    #   data : the list of scalar to print in the text file

    f = open(name, "w")
    for point in data : 
        f.write(str(point))
        f.write('\n')   
    f.close()
    
    return

## Step 0 : The interferometer

## Step 1 : Calibration

Q1 : Plot the output voltage as a function of the input voltage.

Q2 : Fit a sine function to the output.

## Step 2 : Hardware injections

Q1 : Generate the waveform of a $20-20M_\odot$ Binary Black Hole (BBH) at $1\,{\rm Mpc}$ and plot it in the time domain.


Q2 : Use the calibration parameters to translate this waveform in input voltage.

In order to translate this waveform use the maximum amplitude of a $80-80\,{\rm M_\odot}$ BBH at $1\,{\rm Mpc}$ to normalise your waveform.

Q3 : Do the hardware injection and plot the output. Measure also the noise in order to build a Power Spectrum Density during the analysis (same duration for the two time series)

READ THIS : With the temperature variation the calibration stand for a minute. Launch all your program at once to stay calibrated for the hardware injection.

Your signal is in V but we need the reconstrcuted signal to analyse it.

Q4 : Reconstruct the signal (you have to remove the calibration, you might use the saturation function if needed).

Plot the reconstructed signal in time or (even better) frequency domain.

Q5 : Save the noise and the signal in two TXT files.